# CAMELS-DE station map
Generate an interactive Folium map from the CAMELS-DE station geopackage and export it to `assets/interactive-map.html` so it can be embedded on the static website.

**Dependencies**: `geopandas`, `folium`, and their spatial stack (`fiona`, `pyproj`, `shapely`). Install them once per environment, e.g. `pip install geopandas folium`.

In [44]:
from pathlib import Path
import geopandas as gpd
import pandas as pd
import folium

In [45]:
GPKG_PATH = Path("/home/alexd/datasets/CAMELS_DE_v1_1_0/CAMELS_DE_catchment_boundaries/gauging_stations/CAMELS_DE_gauging_stations.gpkg")
TOPO_PATH = Path("/home/alexd/datasets/CAMELS_DE_v1_1_0/CAMELS_DE_topographic_attributes.csv")
HYDRO_PATH = Path("/home/alexd/datasets/CAMELS_DE_v1_1_0/CAMELS_DE_hydrologic_attributes.csv")
DE_BORDERS_PATH = Path("/home/alexd/datasets/germany_shapefile/vg250_ebenen_0101/DE_VG250.gpkg")

EXPORT_PATH = Path("../assets") / "interactive-map.html"

In [46]:
# read gauging stations
stations = gpd.read_file(GPKG_PATH)
stations = stations.to_crs(4326)  # WGS84 for web maps

stations.head()

gauge_id      gauge_name                  geometry
0  DE110000  Kirchen-Hausen  POINT (8.67958 47.92550)
1  DE110010       Möhringen  POINT (8.76010 47.94895)
2  DE110020    Hundersingen  POINT (9.39609 48.07246)
3  DE110030            Berg  POINT (9.73146 48.26627)
4  DE110040      Achstetten  POINT (9.90081 48.26344)

In [47]:
# read attributes
df_topo = pd.read_csv(TOPO_PATH)
df_hydro = pd.read_csv(HYDRO_PATH)

In [48]:
# read Germany borders
de_borders = gpd.read_file(DE_BORDERS_PATH)
de_borders = de_borders.to_crs(4326)  # WGS84
de_borders = de_borders.dissolve().boundary

In [49]:
# drop gauge_name from stations as we use the one from topo attributes
stations = stations.drop(columns=['gauge_name'])

# Merge topographic and hydrologic attributes
stations = stations.merge(df_topo[['gauge_id', 'gauge_name', 'water_body_name', 'federal_state', 'area', 'gauge_elev']], 
                          on='gauge_id', how='left')
stations = stations.merge(df_hydro[['gauge_id', 'flow_period_start', 'flow_period_end']], 
                          on='gauge_id', how='left')

print(f"Merged {len(stations)} stations with attributes")
stations.head()

Merged 1582 stations with attributes


gauge_id                  geometry      gauge_name water_body_name  \
0  DE110000  POINT (8.67958 47.92550)  Kirchen-Hausen           Donau   
1  DE110010  POINT (8.76010 47.94895)       Möhringen           Donau   
2  DE110020  POINT (9.39609 48.07246)    Hundersingen           Donau   
3  DE110030  POINT (9.73146 48.26627)            Berg           Donau   
4  DE110040  POINT (9.90081 48.26344)      Achstetten    Baierzer Rot   

       federal_state     area  gauge_elev flow_period_start flow_period_end  
0  Baden-Württemberg   763.07      661.99        1951-01-01      2020-12-31  
1  Baden-Württemberg   831.29      650.84        1951-01-01      2020-12-31  
2  Baden-Württemberg  2618.60      546.44        1951-01-01      2020-12-31  
3  Baden-Württemberg  4093.96      493.75        1951-01-01      2020-12-31  
4  Baden-Württemberg   272.81      491.35        1951-01-01      2020-12-31

In [59]:
center = [stations.geometry.y.mean(), stations.geometry.x.mean()]
m = folium.Map(location=center, zoom_start=6, tiles='OpenStreetMap')

for idx, row in stations.iterrows():
    geom = row.geometry
    if geom is None or geom.is_empty:
        continue
    
    # Tooltip (on hover): Gauge name and River name
    gauge_name = row.get('gauge_name', 'Unknown')
    river_name = row.get('water_body_name', 'Unknown')
    tooltip_text = f"<b>{gauge_name}</b><br/>{river_name}"
    
    # Popup (on click): Detailed information
    gauge_id = row.get('gauge_id', 'N/A')
    federal_state = row.get('federal_state', 'N/A')
    area = row.get('area', 'N/A')
    gauge_elev = row.get('gauge_elev', 'N/A')
    flow_start = row.get('flow_period_start', 'N/A')
    flow_end = row.get('flow_period_end', 'N/A')
    
    # Format area and elevation with proper units
    area_str = f"{area:.2f}" if pd.notna(area) else "N/A"
    elev_str = f"{gauge_elev:.2f}" if pd.notna(gauge_elev) else "N/A"
    
    popup_html = f"""
    <div style="font-family: Arial, sans-serif; min-width: 200px;">
        <h4 style="margin: 0 0 10px 0; color: #0e7c86;">{gauge_name}</h4>
        <table style="width: 100%; border-collapse: collapse;">
            <tr><td style="padding: 3px;"><b>Gauge ID:</b></td><td style="padding: 3px;">{gauge_id}</td></tr>
            <tr><td style="padding: 3px;"><b>River:</b></td><td style="padding: 3px;">{river_name}</td></tr>
            <tr><td style="padding: 3px;"><b>Federal State:</b></td><td style="padding: 3px;">{federal_state}</td></tr>
            <tr><td style="padding: 3px;"><b>Area:</b></td><td style="padding: 3px;">{area_str} km²</td></tr>
            <tr><td style="padding: 3px;"><b>Elevation:</b></td><td style="padding: 3px;">{elev_str} m+NN</td></tr>
            <tr><td style="padding: 3px;"><b>Flow Period:</b></td><td style="padding: 3px;">{flow_start} to {flow_end}</td></tr>
        </table>
    </div>
    """
    
    folium.CircleMarker(
        location=[geom.y, geom.x],
        radius=6,
        color="#0e7c86",
        fill=True,
        fill_color="#0e7c86",
        fill_opacity=0.7,
        weight=2,
        tooltip=folium.Tooltip(tooltip_text, sticky=True),
        popup=folium.Popup(popup_html, max_width=300)
    ).add_to(m)

# Add Germany borders
folium.GeoJson(
    de_borders,
    name="Germany Borders",
    style_function=lambda x: {'color': 'black', 'weight': 1.75, 'fillOpacity': 0}
).add_to(m)

m.save(EXPORT_PATH)
print(f"Saved interactive map with {len(stations)} stations to {EXPORT_PATH}")
m

Saved interactive map with 1582 stations to ../assets/interactive-map.html
